# Exploration

## Imports

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pandas_profiling as pp
# from ipyleaflet import Map, basemaps, basemap_to_tiles, 
import folium
from geopy import distance
%matplotlib inline

In [2]:
import warnings
warnings.filterwarnings('ignore')

from tqdm import tqdm_notebook, tqdm_pandas
from tqdm.auto import tqdm
import psycopg2

## Connection

In [3]:
con = psycopg2.connect(
  database="postgres", 
  user="postgres", 
  password="test-task", 
  host="ec2-52-15-186-119.us-east-2.compute.amazonaws.com", 
  port="8213"
)

In [4]:
cursor = con.cursor()

In [5]:
cursor.execute("""SELECT table_name FROM information_schema.tables
       WHERE table_schema = 'public'""")
for table in cursor.fetchall():
    print(table)

('offers',)
('pairs',)


##  Look at tables

### What's in

In [6]:
# смотрим на пары

cursor.execute("select * from pairs limit 10")
cursor.fetchone()

(0,
 '32d2e60b11e78e42de5669af512652fc',
 '3c97e4fbadbf873edb82936d9dcef7b5',
 False,
 True)

In [7]:
# смотрим на офферы

cursor.execute("select * from offers limit 10")
cursor.fetchone()

(0,
 '3dddd44ec9b2d96c12d9929a1baf060a',
 'Мы работаем, и у нас безопасно!\n- Заселяем клиентов круглосуточно и дистанционно, без встречи с сотрудником\n- Принимаем оплату бесконтактным способом\n- Дезинфицируем все поверхности в квартире перед заселением и после выезда\n- Останавливаясь у нас, Вы никогда не будете обмануты или введены в заблуждение \n- Фото соответствует действительности \n- У нас широкий выбор апартаментов. Все квартиры имеют удобное расположение, находятся рядом с остановками, магазинами и тп.\n- Мы предоставляем надежные отчетные документы (возможно без проживания)\n- Работаем с юридическими лицами. \n\nУютная, теплая и чистая двухкомнатная квартира в самом центре Втузгородка по ул. Мира 37 недалеко от центра города, ТРЦ Комсомолл ждет своих гостей на СУТКИ, ЧАСЫ, НЕДЕЛИ, МЕСЯЦ !\n\nРядом: УрФУ Мира 19, Институт МЧС Мира 22, Юридическая Академия Комсомольская 21, Суворовское училище, Дендропарк, ЦК "Урал" Студенческая 3, Гуманитарный университет Студенческая 19, ФГ

In [8]:
[desc[0] for desc in cursor.description]

['index',
 'offer_id',
 'description',
 'geo',
 'building',
 'roomscount',
 'floornumber',
 'category',
 'totalarea',
 'userid',
 'publisheduserid',
 'flattype',
 'bargainterms']

###  Counts

In [9]:
cursor.execute("select count(1) from pairs")
cursor.fetchone()

(10000,)

In [10]:
cursor.execute("select count(1) from offers")
cursor.fetchone()

(19266,)

## Postgres to pandas

In [13]:
import pandas as pd
import pandas.io.sql as sqlio

In [14]:
sql = 'select * from pairs'
df_pairs = sqlio.read_sql_query(sql, con)

In [15]:
sql = 'select * from offers'
df_offers = sqlio.read_sql_query(sql, con)

In [16]:
from ast import literal_eval

In [17]:
df_offers.head(1).T

0
index                                                            0
offer_id                          3dddd44ec9b2d96c12d9929a1baf060a
description      Мы работаем, и у нас безопасно!\n- Заселяем кл...
geo              {'countryId': 138, 'undergrounds': [], 'calcul...
building         {'materialType': 'block', 'parking': {'type': ...
roomscount                                                       2
floornumber                                                      2
category                                             dailyFlatRent
totalarea                                                       45
userid                            bd8a8031d43e3eb578f47787ddd246c5
publisheduserid                   bd8a8031d43e3eb578f47787ddd246c5
flattype                                                     rooms
bargainterms     {'price': 1790.0, 'currency': 'rur', 'deposit'...

In [18]:
df_pairs.head()

index                         offer_id1                         offer_id2  \
0      0  32d2e60b11e78e42de5669af512652fc  3c97e4fbadbf873edb82936d9dcef7b5   
1      1  c0c231515e921556c8cdf73894093287  c3f5028d830efec4f5983229773463c7   
2      2  c4ffce989e9347b24a38d59c0cfd289e  95f53b119d44d947df8cea7edf4b0bd1   
3      3  a4720f07160c35184c814d9d3f1c7efb  b922588339c1c7a303dde2511b25e3b5   
4      4  a145e8f719bd71e3d2615f02e9680ebf  345121b878d4d4e4afef4a70ad35d64b   

   is_test  resolution  
0    False        True  
1    False        True  
2    False        True  
3    False        True  
4    False        True

In [19]:
del df_pairs['is_test']

In [20]:
df_pairs['resolution'] = df_pairs['resolution'].astype(int)

In [21]:
df_pairs.head()

index                         offer_id1                         offer_id2  \
0      0  32d2e60b11e78e42de5669af512652fc  3c97e4fbadbf873edb82936d9dcef7b5   
1      1  c0c231515e921556c8cdf73894093287  c3f5028d830efec4f5983229773463c7   
2      2  c4ffce989e9347b24a38d59c0cfd289e  95f53b119d44d947df8cea7edf4b0bd1   
3      3  a4720f07160c35184c814d9d3f1c7efb  b922588339c1c7a303dde2511b25e3b5   
4      4  a145e8f719bd71e3d2615f02e9680ebf  345121b878d4d4e4afef4a70ad35d64b   

   resolution  
0           1  
1           1  
2           1  
3           1  
4           1

In [22]:
df_pairs.resolution.mean()

0.6886

In [24]:
for el in df_offers.category.unique():
    print(el)

dailyFlatRent
houseRent
flatRent
dailyHouseRent
flatSale
landSale
newBuildingFlatSale
roomSale
townhouseSale
houseSale
cottageSale
roomRent
cottageRent
townhouseRent
dailyRoomRent
houseShareSale
houseShareRent
flatShareSale


In [25]:
df_offers = df_offers.set_index("offer_id")

In [26]:
tqdm.pandas('apply')
df_offers.geo = df_offers.geo.progress_apply(literal_eval)
df_offers.bargainterms = df_offers.bargainterms.progress_apply(literal_eval)
df_offers.building = df_offers.building.progress_apply(literal_eval)

In [27]:
df_geo = pd.DataFrame(list(df_offers.geo), index=df_offers.index)
df_bargainterms = pd.DataFrame(list(df_offers.bargainterms), index=df_offers.index)
df_building = pd.DataFrame(list(df_offers.building), index=df_offers.index)

In [28]:
df_building.head(1).T

offer_id                 3dddd44ec9b2d96c12d9929a1baf060a
materialType                                        block
parking                                {'type': 'ground'}
floorsCount                                             5
cranageTypes                                           []
extinguishingSystemTypes                               []
liftTypes                                              []
infrastructure                                         {}
totalArea                                              45
openingHours                                           {}
deadline                                               {}
heatingType                                           NaN
passengerLiftsCount                                   NaN
buildYear                                             NaN
cargoLiftsCount                                       NaN
name                                                  NaN
hasGarbageChute                                       NaN
ceilingHeight                                         NaN
series                                                NaN

In [29]:
df_building.parking = df_building.parking.apply(lambda x: x['type'] if x else None)

In [30]:
df_building.loc['7ad82c425149cc94213fed615183cf50'].deadline

{'quarter': 'first', 'year': 2019, 'isComplete': True}

In [31]:
cranage = df_building.cranageTypes.apply(len)

cranage[cranage>0]

Series([], Name: cranageTypes, dtype: int64)

In [32]:
df_building.deadline.apply(lambda x: x['isComplete'] if 'isComplete' in x.keys() else None).dropna().shape

(1613,)

1613 Новостроек?

In [33]:
df_building.deadline.apply(lambda x: x['isComplete'] if 'isComplete' in x.keys() else None).dropna().mean()

0.09051456912585244

9% завершено

In [34]:
pp.ProfileReport(df_building[[
    'buildYear',
    'cargoLiftsCount',
    'ceilingHeight',
    'floorsCount',
    'hasGarbageChute',
    'heatingType',
    'materialType',
    'name',
    'parking',
    'passengerLiftsCount',
    'series',
    'totalArea'
]])

## Geo-exploration

In [35]:
df_geo.head(1).T

offer_id                                 3dddd44ec9b2d96c12d9929a1baf060a
countryId                                                             138
undergrounds                                                           []
calculatedUndergrounds                                                 []
coordinates                           {'lat': 56.83456, 'lng': 60.654356}
highways                                                               []
railways                                                               []
userInput               Россия, Свердловская область, Екатеринбург, ми...
address                 [{'name': 'Свердловская', 'id': 4612, 'locatio...
district                [{'locationId': 4743, 'id': 289, 'name': 'Киро...
locationPath            {'countryId': 138, 'childToParent': [199906, 4...
publishCoordinates                                                    NaN
jk                                                                    NaN

In [36]:
df_geo.district[0]

[{'locationId': 4743, 'id': 289, 'name': 'Кировский', 'type': 'raion'},
 {'parentId': 289,
  'locationId': 4743,
  'id': 1470,
  'name': 'Втузгородок',
  'type': 'mikroraion'}]

In [37]:
df_geo.userInput.nunique()

11606

11606/19266 (60%) уникальных адресов

In [38]:
df_geo['lat'] = df_geo.coordinates.apply(lambda x: x['lat'])
df_geo['lon'] = df_geo.coordinates.apply(lambda x: x['lng'])

In [39]:
sample1 = df_pairs[df_pairs.resolution==1].sample(100, random_state=42)
sample1_coord = df_geo.loc[list(set(list(sample1.offer_id1) + list(sample1.offer_id2)))][['lat', 'lon']]
sample0 = df_pairs[df_pairs.resolution==0].sample(100, random_state=42)
sample0_coord = df_geo.loc[list(set(list(sample0.offer_id1) + list(sample0.offer_id2)))][['lat', 'lon']]

In [40]:
# dups
from folium.plugins import MarkerCluster

m = folium.Map(
    location=[55.742049, 37.629988],
    zoom_start=9
)

marker_cluster = MarkerCluster().add_to(m)

for marker in sample1_coord.values:
    folium.Marker(marker).add_to(marker_cluster)
m

In [41]:
# no dups

m = folium.Map(
    location=[55.742049, 37.629988],
    zoom_start=9
)
marker_cluster = MarkerCluster().add_to(m)

for marker in sample0_coord.values:
    folium.Marker(marker).add_to(marker_cluster)
m

In [42]:
df_geo.loc[sample1.offer_id1][['lat', 'lon']].shape

(100, 2)

In [45]:
sample1 = df_pairs[df_pairs.resolution==1].sample(1000, random_state=42)
sample1_dist = sample1.apply(
    lambda x: distance.geodesic(
        df_geo.loc[x['offer_id1']][['lat', 'lon']].values,
        df_geo.loc[x['offer_id2']][['lat', 'lon']].values
    ).km,
    axis=1
)

In [46]:
sample0 = df_pairs[df_pairs.resolution==0].sample(1000, random_state=42)
sample0_dist = sample0.apply(
    lambda x: distance.geodesic(
        df_geo.loc[x['offer_id1']][['lat', 'lon']].values,
        df_geo.loc[x['offer_id2']][['lat', 'lon']].values
    ).km,
    axis=1
)

In [47]:
sample1_dist.describe()

count    1000.000000
mean        0.071536
std         0.785235
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max        13.913698
dtype: float64

In [48]:
sample0_dist.describe()

count    1000.000000
mean        0.293648
std         4.233165
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max       126.038684
dtype: float64

In [49]:
import seaborn as sns

In [50]:
fig, axs = plt.subplots(nrows=2)
sns.boxplot(sample1_dist, ax=axs[0])
sns.boxplot(sample0_dist, ax=axs[1])

In [51]:
df_geo.dropna(subset=['coordinates']).shape

(19266, 14)

## bargain - exploration

In [52]:
df_bargainterms.head(3).T

offer_id          3dddd44ec9b2d96c12d9929a1baf060a  \
price                                         1790   
currency                                       rur   
deposit                                       2000   
bargainAllowed                               False   
priceType                                      all   
includedOptions                                 []   
clientFee                                      NaN   
leaseTermType                                  NaN   
agentFee                                       NaN   
prepayMonths                                   NaN   
paymentPeriod                                  NaN   
utilitiesTerms                                 NaN   
bargainPrice                                   NaN   
saleType                                       NaN   
mortgageAllowed                                NaN   
bargainConditions                              NaN   
agentBonus                                     NaN   
tenantsType                                    NaN   
actionId                                       NaN   

offer_id                  7a64d22e18d5a075960d350b24ed2dc4  \
price                                               450000   
currency                                               rur   
deposit                                             450000   
bargainAllowed                                       False   
priceType                                              all   
includedOptions                                         []   
clientFee                                                0   
leaseTermType                                     longTerm   
agentFee                                                 0   
prepayMonths                                             1   
paymentPeriod                                      monthly   
utilitiesTerms     {'includedInPrice': True, 'price': 0.0}   
bargainPrice                                           NaN   
saleType                                               NaN   
mortgageAllowed                                        NaN   
bargainConditions                                      NaN   
agentBonus                                             NaN   
tenantsType                                            NaN   
actionId                                               NaN   

offer_id                  e105393cf6f3c91d9734a0bc903fe82f  
price                                                15000  
currency                                               rur  
deposit                                              15000  
bargainAllowed                                        True  
priceType                                              all  
includedOptions                                         []  
clientFee                                                0  
leaseTermType                                    fewMonths  
agentFee                                                 0  
prepayMonths                                             1  
paymentPeriod                                      monthly  
utilitiesTerms     {'includedInPrice': True, 'price': 0.0}  
bargainPrice                                         14000  
saleType                                               NaN  
mortgageAllowed                                        NaN  
bargainConditions                                      NaN  
agentBonus                                             NaN  
tenantsType                                            NaN  
actionId                                               NaN

In [53]:
for col in df_bargainterms.columns:
    try:
        print(df_bargainterms[col].nunique())
    except:
        print(col + ' - unhashable')

4362
3
327
2
1
includedOptions - unhashable
45
2
37
7
1
utilitiesTerms - unhashable
99
5
2
186
agentBonus - unhashable
4
67


In [54]:
pp.ProfileReport(df_bargainterms[['actionId', 'agentFee', 'bargainAllowed',
       'bargainConditions', 'bargainPrice', 'clientFee', 'currency', 'deposit',
       'leaseTermType', 'mortgageAllowed', 'paymentPeriod',
       'prepayMonths', 'price', 'priceType', 'saleType', 'tenantsType']])

# Save to pickle

In [55]:
df_pairs.to_pickle('../data/df_pairs.pkl')
df_offers.to_pickle('../data/df_offers.pkl')
df_geo.to_pickle('../data/df_geo.pkl')
df_building.to_pickle('../data/df_building.pkl')
df_bargainterms.to_pickle('../data/df_bargainterms.pkl')